In [1]:
#script to evaluate solver with syntetical data

import numpy as np
import pandas as pd
from load_and_process import load_online, process_online, load_offline, process_offline, load_CO2, process_CO2
from lmfit import Parameters, report_fit, minimize, fit_report
from model_funcs import sim_single_exp
from parest_funcs import residuals_all_exp
from plotly.subplots import make_subplots
from copy import deepcopy
import plotly.graph_objs as go
import time
import plotly.express as px

In [2]:
metadata = pd.read_excel("C:/Masterarbeit/Messdaten/metadata.xlsx", index_col = "fermentation")
exp_numbers =[4,5,6,7,8]
y0_dict = {}
c_dict = {}
len_off_div_on = 1
len_off_div_CO2 = 1
Gly_per_Et = 0.22
CO2_mean_p = 1
experiments = ["ferm4","ferm5","ferm6", "ferm7", "ferm8"]


for ferm in experiments:
    x = list(metadata.loc[ferm,["feed_on", "feed_rate","csf", "M_base", "gas_flow", "T"]].values)
    x.append(len_off_div_on)
    x.append(len_off_div_CO2)
    x.append(CO2_mean_p)
    c_dict[ferm] = {"feed_on" : x[0], "feed_rate" : x[1], "csf" : x[2], "M_base" : x[3], "gas_flow" : x[4], "T" : x[5], "wf_on" : x[6], "wf_CO2" : x[7], "pressure" : x[8]}

    y0_dict[ferm] = list(metadata.loc[ferm,["mS0", "mX0", "mE0","V0"]].values)

In [3]:
p0 = Parameters()
p0.add("qsmax", value=3.5, min=0.01, max=5.0 , vary = True)     #Maximum glucose uptake rate [g/(g*h)]
p0.add("qemax", value=0.2361, min=0.15, max=0.35, vary=False)    #Maximum ethanol uptake rate [g/(g*h)]       #value=0.2361, min=0.15, max=0.35, vary=True # value=0.05, min=0.001, max=0.5,  vary=True geht

p0.add("base_coef", value= 0.009, min=0.0001, max =3, vary = True)     #base coefficient [mol/G]
p0.add("qO2max", value= 0.27, min=0.1, max=0.4, vary = True)    #Maximum oxygen uptake rate [g/(g*h)]  , min=0.1
p0.add("qm_max", value=0.01, min=0.0075, max=0.0125, vary = False)  #glucose uptake rate required for maintenance [g/(g*h)]
  
p0.add("Ks", value=0.1, min=0.01, max=1,  vary=False)   #Saturation constant, concentration of glucose at µ = 0.5 µmax [g/L]
p0.add("Ke", value=0.1, min=0.01, max=1, vary=False)    #Saturation constant, concentration of ethanol at µ = 0.5 µmax [g/L]
p0.add("Ki", value=0.1, min=0.01, max=1, vary=False)    #Inhibition constant, glucose inhibits uptake of ethanol [g/L]

p0.add("Yxs_ox", value=0.49, min=0.4, max=0.55, vary=False) #Yield biomass per glucose (oxidative growth) [g/g]
p0.add("Yxs_red", value=0.05, min=0.01, max=0.8, vary=False)    #Yield biomass per glucose (reductive growth) [g/g]
p0.add("Yxe_et", value=0.72, min=0.5, max=0.8, vary=False)      #Yield biomass per ethanol [g/g]
p0.add("Yxg_glyc", value=0.2, min=0.1, max=0.35, vary=False)    #Yield biomass per glycerol [g/g]

#Biomasscomposition paramaters, content H,O,N from paper sonnleitner

p0.add("HX", value=1.79, min=1.77, max=2.1, vary=False) #Stoichiometric hydrogen content of biomass [mol/mol]
p0.add("OX", value=0.57, min=0.54, max=0.63, vary=False) #Stoichiometric oxygen content of biomass [mol/mol]     
p0.add("NX", value=0.15, min=0.14, max=0.16, vary=False) #Stoichiometric nitrogen content of biomass [mol/mol]

p0.add("g_e", value = 0.2163628) #determined experimentally: formation glycerol per ethanol [g/g]

#new in parest_funcs generated
p0.add("YCO2s_m", value = 1.4657061593696088, vary = False)
p0.add("Yes_red", value = 0.4255007)
p0.add("Ygs_red", value = 0.09206254)

p0.add("YCO2s_ox", value = 0.604357)
p0.add("YCO2s_red", value = 0.4328713)
p0.add("YCO2e_et", value = 0.644938)
p0.add("YCO2g_glyc", value = 1.082053)

p0.add("YO2s_ox", value = 0.4081016)
p0.add("YO2e_et", value = 1.117485)
p0.add("YO2g_glyc", value = 1.894468)

In [4]:
p1 = deepcopy(p0)
t_sim1 = np.linspace(0,10, 50)

sim_dict = {}
for ferm in experiments:
    sim_dict[ferm] = sim_single_exp(t_grid = t_sim1, y0 = y0_dict[ferm], p = p1, c = c_dict[ferm])

[df.drop(["V"], inplace=True, axis=1) for df in sim_dict.values()]

[None, None, None, None, None]

In [5]:
line_markers = "lines+markers"
line = "lines"
markers = "markers"
dict_longnames = {"ferm4" : "Fermentation 4", "ferm5" : "Fermentation 5", "ferm6" : "Fermentation 6", "ferm7" : "Fermentation 7", "ferm8" : "Fermentation 8"}
color_dict = {"base_rate" : "cyan", "cX" : "red", "cS" : "green", "cE" : "blue", "CO2" : "orange"}

for ferm, df in sim_dict.items():
    fig = px.scatter(df)
    


    fig.update_yaxes(title_text="Biomass(cX) [g/L] , Glucose(cS) [g/L] , Ethanol(cE) [g/L],<br><br> Base consumption rate [ml/h], CO2 [vol. %]", secondary_y=False , title_standoff = 20)
    fig.update_xaxes(title_text= "Time [h]")
    fig.update_layout(title_text = dict_longnames[ferm], title_x=0.5)     
    
    fig.update_layout(legend=dict(x = 1.1))
            
    fig.show()

In [6]:
sim_noise_dict = {}
for ferm, df in sim_dict.items():
    noise = np.random.normal(0, 0.05, np.shape(df))
    df = df * (1+ noise)
    sim_noise_dict[ferm] = df

In [7]:
line_markers = "lines+markers"
line = "lines"
markers = "markers"
dict_longnames = {"ferm4" : "Fermentation 4", "ferm5" : "Fermentation 5", "ferm6" : "Fermentation 6", "ferm7" : "Fermentation 7", "ferm8" : "Fermentation 8"}

for ferm, df in sim_noise_dict.items():
    fig = px.scatter(df)
    fig


    fig.update_yaxes(title_text="Biomass(cX) [g/L] , Glucose(cS) [g/L] , Ethanol(cE) [g/L],<br><br> Base consumption rate [ml/h], CO2 [vol. %]", secondary_y=False , title_standoff = 20)
    fig.update_xaxes(title_text= "Time [h]")
    fig.update_layout(title_text = dict_longnames[ferm], title_x=0.5)     
    
    fig.update_layout(legend=dict(x = 1.1))
            
    fig.show()

In [8]:
synth_datasets_dict = {}

for ferm, df in sim_noise_dict.items():
    synth_datasets_dict[ferm] = [df]

In [9]:
p = Parameters()
p.add("qsmax", value=2.5, min=0.01, max=5.0 , vary = True)     #Maximum glucose uptake rate [g/(g*h)]
p.add("qemax", value=0.17, min=0.15, max=0.35, vary=True)    #Maximum ethanol uptake rate [g/(g*h)]       #value=0.2361, min=0.15, max=0.35, vary=True # value=0.05, min=0.001, max=0.5,  vary=True geht

p.add("base_coef", value= 0.1, min=0.0001, max =3, vary = True)     #base coefficient [???]
p.add("qO2max", value= 0.15, min=0.1, max=0.4, vary = True)    #Maximum oxygen uptake rate [g/(g*h)]  , min=0.1
p.add("qm_max", value=0.01, min=0.0075, max=0.0125, vary = False)  #glucose uptake rate required for maintenance [g/(g*h)]
  
p.add("Ks", value=0.1, min=0.01, max=1,  vary=False)   #Saturation constant, concentration of glucose at µ = 0.5 µmax [g/L]
p.add("Ke", value=0.1, min=0.01, max=1, vary=False)    #Saturation constant, concentration of ethanol at µ = 0.5 µmax [g/L]
p.add("Ki", value=0.1, min=0.01, max=1, vary=False)    #Inhibition constant, glucose inhibits uptake of ethanol [g/L]

p.add("Yxs_ox", value=0.49, min=0.4, max=0.55, vary=False) #Yield biomass per glucose (oxidative growth) [g/g]
p.add("Yxs_red", value=0.05, min=0.01, max=0.8, vary=False)    #Yield biomass per glucose (reductive growth) [g/g]
p.add("Yxe_et", value=0.72, min=0.5, max=0.8, vary=False)      #Yield biomass per ethanol [g/g]
p.add("Yxg_glyc", value=0.2, min=0.1, max=0.35, vary=False)    #Yield biomass per glycerol [g/g]

#Biomasscomposition paramaters, content H,O,N from paper sonnleiter

p.add("HX", value=1.79, min=1.77, max=2.1, vary=False) #Stoichiometric hydrogen content of biomass [mol/mol]
p.add("OX", value=0.57, min=0.54, max=0.63, vary=False) #Stoichiometric oxygen content of biomass [mol/mol]     
p.add("NX", value=0.15, min=0.14, max=0.16, vary=False) #Stoichiometric nitrogen content of biomass [mol/mol]

p.add("g_e", value = 0.2163628) #determined experimentally: formation glycerol per ethanol [g/g]

In [10]:
start = time.time()

result = minimize(residuals_all_exp, p, args=(y0_dict, c_dict, synth_datasets_dict), method='leastsq', nan_policy= "omit")

end = time.time()
print(end - start)

134.1417589187622


In [11]:
report_fit(result)

[[Fit Statistics]]
    # fitting method   = leastsq
    # function evals   = 97
    # data points      = 1250
    # variables        = 5
    chi-square         = 54.5337332
    reduced chi-square = 0.04380220
    Akaike info crit   = -3905.09920
    Bayesian info crit = -3879.44471
[[Variables]]
    qsmax:       3.53139872 +/- 0.02149352 (0.61%) (init = 2.5)
    qemax:       0.23622533 +/- 0.04280588 (18.12%) (init = 0.17)
    base_coef:   0.00899152 +/- 8.8444e-05 (0.98%) (init = 0.1)
    qO2max:      0.26930874 +/- 1.4511e-05 (0.01%) (init = 0.15)
    qm_max:      0.01 (fixed)
    Ks:          0.1 (fixed)
    Ke:          0.1 (fixed)
    Ki:          0.1 (fixed)
    Yxs_ox:      0.49 (fixed)
    Yxs_red:     0.05 (fixed)
    Yxe_et:      0.72 (fixed)
    Yxg_glyc:    0.2 (fixed)
    HX:          1.79 (fixed)
    OX:          0.57 (fixed)
    NX:          0.15 (fixed)
    g_e:         0.20932785 +/- 0.00620480 (2.96%) (init = 0.2163628)
    YCO2x_ox:    1.233382 (fixed)
    YCO2s_ox: 

In [12]:
#creating data with new model parameters generated from fit
p_new = result.params
fit_dict = {}
t_sim = np.linspace(0,12, 2001) #timeline for simulation

for ferm, y0 in y0_dict.items():
    sim_exp = sim_single_exp(t_sim, y0, p_new, c_dict[ferm])
    fit_dict[ferm] = sim_exp 

In [13]:
#show results for all variables
line_markers = "lines+markers"
line = "lines"
markers = "markers"
dict_longnames = {"ferm4" : "Fermentation 4", "ferm5" : "Fermentation 5", "ferm6" : "Fermentation 6", "ferm7" : "Fermentation 7", "ferm8" : "Fermentation 8"}

color_dict = {"base_rate" : "cyan", "cX" : "red", "cS" : "green", "cE" : "blue", "CO2" : "orange"}
#color_dict2 = {"base_rate" : "steelblue", "cX" : "crimson", "cS" : "darkgreen", "cE" : "aquamarine", "CO2" : "darkorange"}

for ferm, df_list in synth_datasets_dict.items():
    fig = make_subplots( specs=[[{"secondary_y": True}]])

    for df_dat in df_list:
        
        for column in df_dat:
            secondary_y_flag = column  in ["base_rate", "CO2"]

            fig.add_trace(go.Scatter(x= df_dat.index, y= df_dat[column], name= column, mode = markers, marker = dict(color = color_dict[column], size = 5, symbol = "x")), secondary_y=secondary_y_flag)


    #fit data add
    fig.add_trace( 
        go.Scatter(x= t_sim, y= fit_dict[ferm]["base_rate"], name= "base_rate_fitted", mode = line, marker = dict(color = "cyan", opacity = 0.05)), 
        secondary_y=True,) #"steelblue"
    
    fig.add_trace( 
        go.Scatter(x= t_sim, y= fit_dict[ferm]["cX"], name= "cX_fitted", mode = line, marker = dict(color = "red", opacity = 0.05)), 
        secondary_y=False,) #"crimson"
    
    fig.add_trace( 
        go.Scatter(x= t_sim, y= fit_dict[ferm]["cS"], name= "cS_fitted", mode = line, marker = dict(color = "green", opacity = 0.05)), 
        secondary_y=False,) #"darkgreen"
    

    fig.add_trace( 
        go.Scatter(x= t_sim, y= fit_dict[ferm]["cE"], name= "cE_fitted", mode = line, marker = dict(color = "blue", opacity = 0.05)), 
        secondary_y=False,) #"aquamarine"
    

    fig.add_trace( 
        go.Scatter(x= t_sim, y= fit_dict[ferm]["CO2"], name= "CO2_fitted", mode = line, marker = dict(color = "orange", opacity = 0.05)), 
        secondary_y=True,) #"darkorange"

    fig.update_yaxes(title_text="Biomass(cX) [g/L] , Glucose(cS) [g/L] , Ethanol(cE) [g/L]", secondary_y=False , title_standoff = 20 )
    fig.update_yaxes(title_text="Base consumption rate [ml/h], CO2 [vol. %]", secondary_y=True, title_standoff = 20)
    fig.update_xaxes(title_text= "Time [h]")
    fig.update_layout(title_text = dict_longnames[ferm], title_x=0.5)     #font = dict(size = 10, family = "areal", color = "black")# , font = dict(color = "black")
    #fig.update_layout(width=1000)
    fig.update_layout(legend=dict(x = 1.1))
            
    fig.show()

In [14]:
#Only Offline data
line_markers = "lines+markers"
line = "lines"
markers = "markers"
dict_longnames = {"ferm4" : "Fermentation 4", "ferm5" : "Fermentation 5", "ferm6" : "Fermentation 6", "ferm7" : "Fermentation 7", "ferm8" : "Fermentation 8"}

color_dict = {"base_rate" : "cyan", "cX" : "red", "cS" : "green", "cE" : "blue", "CO2" : "orange"}
filter_off = ["base_rate", "CO2"]


for ferm, df_list in synth_datasets_dict.items():
    fig = make_subplots( specs=[[{"secondary_y": True}]])

    for df_dat in df_list:
        
        for column in df_dat:

            if column not in filter_off:
                secondary_y_flag = column  in ["base_rate", "CO2"]     #filtering only for off

                fig.add_trace(go.Scatter(x= df_dat.index, y= df_dat[column], name= column, mode = markers, marker = dict(color = color_dict[column], size = 5, symbol = "x")),  secondary_y=secondary_y_flag) #line = dict(dash = "dot")),

    
    fig.add_trace( 
        go.Scatter(x= t_sim, y= fit_dict[ferm]["cX"], name= "cX_fitted", mode = line, marker = dict(color = "red")), 
        secondary_y=False,) #"crimson"
    
    fig.add_trace( 
        go.Scatter(x= t_sim, y= fit_dict[ferm]["cS"], name= "cS_fitted", mode = line, marker = dict(color = "green")), 
        secondary_y=False,) #"darkgreen"
    

    fig.add_trace( 
        go.Scatter(x= t_sim, y= fit_dict[ferm]["cE"], name= "cE_fitted", mode = line, marker = dict(color = "blue")), 
        secondary_y=False,) #"aquamarine"
    

    fig.update_yaxes(title_text="Biomass(cX) [g/L] , Glucose(cS) [g/L] , Ethanol(cE) [g/L]", secondary_y=False , title_standoff = 20 )
    #fig.update_yaxes(title_text="Base_rate [ml/h], CO2 [vol. %]", secondary_y=True, title_standoff = 20)
    fig.update_xaxes(title_text= "Time [h]")
    #fig.update_layout(title_text = dict_longnames[ferm], title_x=0.5)     #font = dict(size = 10, family = "areal", color = "black")# , font = dict(color = "black")
    #fig.update_layout(width=1000)
    fig.update_layout(legend=dict(x = 1.1))
            
    fig.show()

In [15]:
#Online + CO2 data
line_markers = "lines+markers"
line = "lines"
markers = "markers"
dict_longnames = {"ferm4" : "Fermentation 4", "ferm5" : "Fermentation 5", "ferm6" : "Fermentation 6", "ferm7" : "Fermentation 7", "ferm8" : "Fermentation 8"}

color_dict = {"base_rate" : "cyan", "cX" : "red", "cS" : "green", "cE" : "blue", "CO2" : "orange"}
filter_off = ["cX", "cS", "cE"]


for ferm, df_list in synth_datasets_dict.items():
    fig = make_subplots( specs=[[{"secondary_y": True}]])

    for df_dat in df_list:
        
        for column in df_dat:

            if column not in filter_off:
                #secondary_y_flag = column  in ["base_rate", "CO2"]     #filtering only for off

                fig.add_trace(go.Scatter(x= df_dat.index, y= df_dat[column], name= column, mode = markers, marker = dict(color = color_dict[column], size = 5, symbol = "x")),  secondary_y=False) #line = dict(dash = "dot")),

    
    fig.add_trace( 
        go.Scatter(x= t_sim, y= fit_dict[ferm]["base_rate"], name= "base_rate_fitted", mode = line, marker = dict(color = "cyan")), 
        secondary_y=False,) #"crimson"
    
    fig.add_trace( 
        go.Scatter(x= t_sim, y= fit_dict[ferm]["CO2"], name= "CO2_fitted", mode = line, marker = dict(color = "orange")), 
        secondary_y=False,) #"darkgreen"
    


    fig.update_yaxes(title_text="Base consumption rate [ml/h], CO2 [vol. %]", secondary_y=False , title_standoff = 20 )
    #fig.update_yaxes(title_text="Base_rate [ml/h], CO2 [vol. %]", secondary_y=True, title_standoff = 20)
    fig.update_xaxes(title_text= "Time [h]")
    #fig.update_layout(title_text = dict_longnames[ferm], title_x=0.5)     #font = dict(size = 10, family = "areal", color = "black")# , font = dict(color = "black")
    #fig.update_layout(width=1000)
    fig.update_layout(legend=dict(x = 1.1))
            
    fig.show()